In [ ]:
import pandas as pd
import re
import warnings
warnings.filterwarnings("ignore")

In [6]:
columns=['target','ids','date','flag','user','text']
df=pd.read_csv('twitter.csv',encoding='ISO-8859-1',names=columns)
df.head()

target         ids                          date      flag  \
0       0  1467810369  Mon Apr 06 22:19:45 PDT 2009  NO_QUERY   
1       0  1467810672  Mon Apr 06 22:19:49 PDT 2009  NO_QUERY   
2       0  1467810917  Mon Apr 06 22:19:53 PDT 2009  NO_QUERY   
3       0  1467811184  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   
4       0  1467811193  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   

              user                                               text  
0  _TheSpecialOne_  @switchfoot http://twitpic.com/2y1zl - Awww, t...  
1    scotthamilton  is upset that he can't update his Facebook by ...  
2         mattycus  @Kenichan I dived many times for the ball. Man...  
3          ElleCTF    my whole body feels itchy and like its on fire   
4           Karoli  @nationwideclass no, it's not behaving at all....

In [7]:
dataset=df[['text','target']]
dataset.head(1)

text  target
0  @switchfoot http://twitpic.com/2y1zl - Awww, t...       0

In [8]:
dataset['target'].unique()

array([0, 4], dtype=int64)

In [9]:
dataset['target']=dataset['target'].replace(4,1)

In [10]:
dataset['target'].unique()

array([0, 1], dtype=int64)

In [11]:
dataset.text[0]

"@switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D"

#Step 1: Remove URL

In [12]:
pattern=re.compile(r'https?://\S+|www\.\S+')
pattern.sub(r'','Twitter Sentiment Analysis Data set available at https://www.kaggle.com/datasets/kazanova/sentiment140')

'Twitter Sentiment Analysis Data set available at '

In [13]:
def remove_url(text):
  pattern=re.compile(r'https?://\S+|www\.\S+')
  return pattern.sub(r'',text)

In [14]:
dataset['text']=dataset['text'].apply(lambda x: remove_url(x))

In [15]:
dataset['text'][0]

"@switchfoot  - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D"

#Step 2: Remove HTML Tags

In [16]:
def remove_tags(text):
  pattern=re.compile(r'<.*?>')
  return pattern.sub(r'',text)

In [17]:
dataset['text']=dataset['text'].apply(lambda x: remove_tags(x))

In [18]:
dataset['text'][0]

"@switchfoot  - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D"

#Step 3: Handling Emojis

In [19]:
#Emojis
emojis = {':)': 'smile', ':-)': 'smile', ';d': 'wink',';D': 'wink',':-E': 'vampire', ':(': 'sad',
          ':-(': 'sad', ':-<': 'sad', ':P': 'raspberry', ':O': 'surprised',
          ':-@': 'shocked', ':@': 'shocked',':-$': 'confused', ':\\': 'annoyed',
          ':#': 'mute', ':X': 'mute', ':^)': 'smile', ':-&': 'confused', '$_$': 'greedy',
          '@@': 'eyeroll', ':-!': 'confused', ':-D': 'smile', ':-0': 'yell', 'O.o': 'confused',
          '<(-_-)>': 'robot', 'd[-_-]b': 'dj', ":'-)": 'sadsmile', ';)': 'wink',
          ';-)': 'wink', 'O:-)': 'angel','O*-)': 'angel','(:-D': 'gossip', '=^.^=': 'cat'}


In [20]:
def handle_emoji(text):
  for emoji in emojis.keys():
    text=text.replace(emoji,"Emoji"+emojis[emoji])
  return text

In [21]:
handle_emoji("@switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D")

"@switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. Emojiwink"

In [22]:
dataset['text']=dataset['text'].apply(lambda x: handle_emoji(x))

In [23]:
dataset['text'][0]

"@switchfoot  - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. Emojiwink"

#Step 4: User Handling

In [24]:
def user_handle(text):
  pattern=re.compile(r'@[^\s]+')
  text=pattern.sub("TUser",text)
  return text
dataset['text']=dataset['text'].apply(lambda x: user_handle(x))

#Step 5: Punctuation Removal

In [25]:
import string

In [26]:
punc=string.punctuation

In [27]:
def remove_punc(text):
  return text.translate(str.maketrans("","",punc))

In [28]:
remove_punc('LOL! It was very funny. ROFL' )

'LOL It was very funny ROFL'

In [29]:
dataset['text']=dataset['text'].apply(lambda x: remove_punc(x))

#Step 6: Chat Word Treatment

In [30]:
slang="slang.txt"

In [31]:
slang

'slang.txt'

In [32]:
with open(slang,'r') as f:
    
    lines=f.readlines()

In [33]:
lines

['AFAIK=As Far As I Know\n',
 'AFK=Away From Keyboard\n',
 'ASAP=As Soon As Possible\n',
 'ATK=At The Keyboard\n',
 'ATM=At The Moment\n',
 'A3=Anytime, Anywhere, Anyplace\n',
 'BAK=Back At Keyboard\n',
 'BBL=Be Back Later\n',
 'BBS=Be Back Soon\n',
 'BFN=Bye For Now\n',
 'B4N=Bye For Now\n',
 'BRB=Be Right Back\n',
 'BRT=Be Right There\n',
 'BTW=By The Way\n',
 'B4=Before\n',
 'B4N=Bye For Now\n',
 'CU=See You\n',
 'CUL8R=See You Later\n',
 'CYA=See You\n',
 'FAQ=Frequently Asked Questions\n',
 'FC=Fingers Crossed\n',
 "FWIW=For What It's Worth\n",
 'FYI=For Your Information\n',
 'GAL=Get A Life\n',
 'GG=Good Game\n',
 'GN=Good Night\n',
 'GMTA=Great Minds Think Alike\n',
 'GR8=Great!\n',
 'G9=Genius\n',
 'IC=I See\n',
 'ICQ=I Seek you (also a chat program)\n',
 'ILU=ILU: I Love You\n',
 'IMHO=In My Honest/Humble Opinion\n',
 'IMO=In My Opinion\n',
 'IOW=In Other Words\n',
 'IRL=In Real Life\n',
 'KISS=Keep It Simple, Stupid\n',
 'LDR=Long Distance Relationship\n',
 'LMAO=Laugh My A..

In [34]:
lines[0].split('=')[1][:-1]

'As Far As I Know'

In [35]:
lines[0].split("=")[0]

'AFAIK'

In [36]:
chat_words=dict()
for i in range(len(lines)):
  chat_words[(lines[i].split('='))[0]]=(lines[i].split('='))[1][:-1]

In [37]:
chat_words

{'AFAIK': 'As Far As I Know',
 'AFK': 'Away From Keyboard',
 'ASAP': 'As Soon As Possible',
 'ATK': 'At The Keyboard',
 'ATM': 'At The Moment',
 'A3': 'Anytime, Anywhere, Anyplace',
 'BAK': 'Back At Keyboard',
 'BBL': 'Be Back Later',
 'BBS': 'Be Back Soon',
 'BFN': 'Bye For Now',
 'B4N': 'Bye For Now',
 'BRB': 'Be Right Back',
 'BRT': 'Be Right There',
 'BTW': 'By The Way',
 'B4': 'Before',
 'CU': 'See You',
 'CUL8R': 'See You Later',
 'CYA': 'See You',
 'FAQ': 'Frequently Asked Questions',
 'FC': 'Fingers Crossed',
 'FWIW': "For What It's Worth",
 'FYI': 'For Your Information',
 'GAL': 'Get A Life',
 'GG': 'Good Game',
 'GN': 'Good Night',
 'GMTA': 'Great Minds Think Alike',
 'GR8': 'Great!',
 'G9': 'Genius',
 'IC': 'I See',
 'ICQ': 'I Seek you (also a chat program)',
 'ILU': 'ILU: I Love You',
 'IMHO': 'In My Honest/Humble Opinion',
 'IMO': 'In My Opinion',
 'IOW': 'In Other Words',
 'IRL': 'In Real Life',
 'KISS': 'Keep It Simple, Stupid',
 'LDR': 'Long Distance Relationship',
 'LM

In [38]:
def chat_word_treatment(text):
  new_text=[]
  for w in text.split():
    if w in chat_words:
      new_text.append(chat_words[w])
    else:
      new_text.append(w)
  return " ".join(new_text)

In [39]:
chat_word_treatment(remove_punc("LOL! It was very funny. ROFL"))

'Laughing out loud It was very funny Rolling On The Floor Laughing'

In [40]:
dataset['text']=dataset['text'].apply(lambda x: chat_word_treatment(x))

In [41]:
dataset['text'][0]

'TUser Awww thats a bummer You shoulda got David Carr of Third Day to do it Emojiwink'

#Step 7: Make Lower Case

In [42]:
dataset['text']=dataset['text'].str.lower()

#Step 8: Spelling Correction

In [46]:
pip install TextBlob

     -------------------------------------- 636.8/636.8 kB 2.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [47]:
from textblob import TextBlob

In [48]:
inc_Text="Helllo ! How are you?"

In [49]:
str(TextBlob(inc_Text).correct())

'Hello ! Now are you?'

In [50]:
def spelling_correct(text):
  return str(TextBlob(inc_Text).correct())

In [83]:
dataset['text']=dataset['text'].apply(lambda x: spelling_correct(x))

#Step 9: Tokenization

In [51]:
import nltk
nltk.download('punkt')
from nltk.tokenize import word_tokenize, sent_tokenize

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Admin\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [52]:
def word_token(text):
  return word_tokenize(text)

In [53]:
dataset['text']=dataset['text'].apply(lambda x: word_token(x))

In [55]:
word_token("I love pizza")

['I', 'love', 'pizza']

#Step 10: Stop Word Removal

In [56]:
text1=word_token(("I am loving pizza").lower())

In [57]:
from nltk.corpus import stopwords

In [58]:
nltk.download('stopwords')


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Admin\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [59]:
print(stopwords.words('english'))

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [60]:
st_w=stopwords.words('english')

In [61]:
clean_text=[word for word in text1 if word not in st_w]

In [62]:
clean_text

['loving', 'pizza']

In [63]:
" ".join(clean_text)

'loving pizza'

In [64]:
from functools import lru_cache

@lru_cache(maxsize=50000)
def remove_stop_words(text):
    
    text=text.split()
    clean_text=[word for word in text if word not in st_w]

    return clean_text

remove_stop_words('My name is Samriddh Shetty')

['My', 'name', 'Samriddh', 'Shetty']

#Step 11: Stemming

In [65]:
from nltk.stem.porter import PorterStemmer
st=PorterStemmer()

In [66]:
st.stem("caring")

'care'

In [67]:
from nltk.stem.porter import PorterStemmer
st = nltk.PorterStemmer()
stem = lru_cache(maxsize=50000)(st.stem)
def stemming_on_text(data):

    text = [stem(word) for word in data]
    return text
dataset['text']= dataset['text'].apply(lambda x: stemming_on_text(x))
dataset['text'].head()

0    [tuser, awww, that, a, bummer, you, shoulda, g...
1    [is, upset, that, he, cant, updat, hi, faceboo...
2    [tuser, i, dive, mani, time, for, the, ball, m...
3    [my, whole, bodi, feel, itchi, and, like, it, ...
4    [tuser, no, it, not, behav, at, all, im, mad, ...
Name: text, dtype: object

In [68]:
from nltk.stem import WordNetLemmatizer
nltk.download('wordnet')
nltk.download('omw-1.4')
lm = nltk.WordNetLemmatizer()
lemmatize = lru_cache(maxsize=50000)(lm.lemmatize)
def lemmatizer_on_text(data):
    text = [lemmatize(word) for word in data]
    return text
dataset['text'] = dataset['text'].apply(lambda x: lemmatizer_on_text(x))
dataset['text'].head()

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Admin\AppData\Roaming\nltk_data...
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\Admin\AppData\Roaming\nltk_data...


0    [tuser, awww, that, a, bummer, you, shoulda, g...
1    [is, upset, that, he, cant, updat, hi, faceboo...
2    [tuser, i, dive, mani, time, for, the, ball, m...
3    [my, whole, bodi, feel, itchi, and, like, it, ...
4    [tuser, no, it, not, behav, at, all, im, mad, ...
Name: text, dtype: object

In [69]:
dataset["text"]=dataset["text"].apply(lambda x:" ".join(x))

In [70]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split

In [71]:
X_train,X_test,y_train,y_test= train_test_split(dataset["text"],dataset["target"],test_size=0.20,random_state=0)

In [72]:
tfidf_Vector =TfidfVectorizer(max_features=500000,ngram_range=(1,3),stop_words ="english")

In [73]:
X_train_tdif = tfidf_Vector.fit_transform(X_train)
X_test_tdif = tfidf_Vector.transform(X_test)

In [74]:
X_train_tdif.shape

(1280000, 500000)

In [75]:
for i,feature in enumerate(tfidf_Vector.get_feature_names_out()):
    print(i,feature)

0 00
1 000
2 000 follow
3 0000
4 0001
5 001
6 007
7 008
8 008 restaur
9 008 restaur moon
10 01
11 010
12 0100
13 0130
14 016
15 02
16 0200
17 0230
18 026
19 03
20 0330
21 04
22 0400
23 0430
24 05
25 050
26 0500
27 0530
28 06
29 0600
30 0630
31 0655
32 07
33 0708
34 0730
35 08
36 0800
37 0809
38 0830
39 09
40 09 babi
41 09 graduat
42 09 ha
43 09 im
44 09 lt3
45 09 miss
46 09 oh
47 09 wa
48 0900
49 09011
50 09011 32
51 09011 32 22
52 090909
53 0910
54 0930
55 093m3
56 099
57 0f
58 0ff
59 0g
60 0h
61 0k
62 0mg
63 0n
64 0ne
65 0o
66 0r
67 0ut
68 10
69 10 000
70 10 10
71 10 11
72 10 12
73 10 12 hour
74 10 13
75 10 15
76 10 20
77 10 30
78 10 alpha
79 10 alreadi
80 10 amp
81 10 away
82 10 bad
83 10 batteri
84 10 bb10
85 10 bb10 start
86 10 bed
87 10 befor
88 10 beta
89 10 better
90 10 billion
91 10 breakfast
92 10 buck
93 10 busi
94 10 card
95 10 cat
96 10 cent
97 10 clock
98 10 come
99 10 day
100 10 day ago
101 10 day dont
102 10 day forecast
103 10 day im
104 10 day left
105 10 day school
1

26308 awsum
26309 awt
26310 awthank
26311 awthat
26312 awu
26313 awul
26314 aww
26315 aww ador
26316 aww aha
26317 aww aint
26318 aww alright
26319 aww alway
26320 aww amaz
26321 aww amp
26322 aww andi
26323 aww anoth
26324 aww anyth
26325 aww arent
26326 aww atleast
26327 aww aw
26328 aww awesom
26329 aww aww
26330 aww babe
26331 aww babi
26332 aww bad
26333 aww bad im
26334 aww bb
26335 aww bbi
26336 aww beauti
26337 aww believ
26338 aww best
26339 aww best friend
26340 aww bet
26341 aww better
26342 aww big
26343 aww birthday
26344 aww bless
26345 aww bless hope
26346 aww bless ya
26347 aww boo
26348 aww boy
26349 aww bradi
26350 aww break
26351 aww brilliant
26352 aww broke
26353 aww brother
26354 aww bummer
26355 aww busi
26356 aww buy
26357 aww bye
26358 aww came
26359 aww care
26360 aww cat
26361 aww chang
26362 aww cheer
26363 aww class
26364 aww close
26365 aww cmon
26366 aww come
26367 aww congrat
26368 aww congratul
26369 aww cool
26370 aww crap
26371 aww cri
26372 aww cuddl

68472 click drag
68473 click email
68474 click follow
68475 click follow button
68476 click game
68477 click got
68478 click heel
68479 click heel time
68480 click heel togeth
68481 click hi
68482 click home
68483 click icon
68484 click im
68485 click just
68486 click left
68487 click like
68488 click link
68489 click link dont
68490 click link just
68491 click link right
68492 click listen
68493 click login
68494 click lol
68495 click make
68496 click mous
68497 click new
68498 click nois
68499 click noth
68500 click noth happen
68501 click page
68502 click peopl
68503 click photo
68504 click pic
68505 click pictur
68506 click pictur tab
68507 click plu
68508 click plu sign
68509 click profil
68510 click quotemojiwinkelet
68511 click quotemojiwinkelet currentquot
68512 click read
68513 click realiz
68514 click repli
68515 click right
68516 click sad
68517 click save
68518 click say
68519 click set
68520 click site
68521 click star
68522 click submit
68523 click thank
68524 click thi
6

96231 did relax
96232 did releas
96233 did rememb
96234 did remind
96235 did remix
96236 did remov
96237 did replac
96238 did repli
96239 did report
96240 did request
96241 did research
96242 did respond
96243 did rest
96244 did restor
96245 did return
96246 did review
96247 did revis
96248 did richard
96249 did rid
96250 did ride
96251 did right
96252 did right lol
96253 did right thing
96254 did ring
96255 did road
96256 did rob
96257 did rock
96258 did room
96259 did round
96260 did rubbish
96261 did rubi
96262 did ruin
96263 did run
96264 did run away
96265 did ryan
96266 did sad
96267 did sad face
96268 did sadli
96269 did said
96270 did sale
96271 did saturday
96272 did save
96273 did saw
96274 did say
96275 did say anyth
96276 did say day
96277 did say didnt
96278 did say good
96279 did say goodby
96280 did say hate
96281 did say hello
96282 did say hi
96283 did say im
96284 did say like
96285 did say lol
96286 did say loud
96287 did say someth
96288 did say thi
96289 did say wa

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



tuser im north
419801 tuser im noth
419802 tuser im nt
419803 tuser im nurs
419804 tuser im nz
419805 tuser im oahu
419806 tuser im ob
419807 tuser im offend
419808 tuser im offic
419809 tuser im offici
419810 tuser im offlin
419811 tuser im ok
419812 tuser im okay
419813 tuser im old
419814 tuser im older
419815 tuser im onli
419816 tuser im onlin
419817 tuser im open
419818 tuser im opposit
419819 tuser im orang
419820 tuser im origin
419821 tuser im outsid
419822 tuser im outta
419823 tuser im pack
419824 tuser im pain
419825 tuser im paint
419826 tuser im parent
419827 tuser im pari
419828 tuser im parti
419829 tuser im partial
419830 tuser im pas
419831 tuser im past
419832 tuser im pay
419833 tuser im pc
419834 tuser im peopl
419835 tuser im person
419836 tuser im philippin
419837 tuser im philli
419838 tuser im phone
419839 tuser im pic
419840 tuser im pick
419841 tuser im pink
419842 tuser im piss
419843 tuser im pj
419844 tuser im place
419845 tuser im plan
419846 tuser im pla

455970 w00000t
455971 w000t
455972 w00t
455973 w00t got
455974 w00t w00t
455975 w0rk
455976 w0rk w0rk
455977 w0rld
455978 w0rri
455979 w0w
455980 w1
455981 w1f
455982 w2
455983 w3
455984 w3c
455985 w4
455986 w4 beij
455987 w4 beij hi
455988 w4m
455989 w7
455990 w8
455991 w8 till
455992 w880i
455993 w8in
455994 w8ing
455995 wa
455996 wa 07
455997 wa 10
455998 wa 10 min
455999 wa 10 minut
456000 wa 10 year
456001 wa 10 yearsold
456002 wa 100
456003 wa 1000
456004 wa 1000th
456005 wa 100th
456006 wa 103
456007 wa 10th
456008 wa 10yr
456009 wa 10yr ago
456010 wa 11
456011 wa 112
456012 wa 11pm
456013 wa 12
456014 wa 1215
456015 wa 13
456016 wa 13 wa
456017 wa 13 year
456018 wa 13th
456019 wa 14
456020 wa 140
456021 wa 140 charact
456022 wa 15
456023 wa 15 hour
456024 wa 15 min
456025 wa 150
456026 wa 16
456027 wa 16 year
456028 wa 16th
456029 wa 17
456030 wa 17th
456031 wa 18
456032 wa 19
456033 wa 1st
456034 wa 1st time
456035 wa 20
456036 wa 20 minut
456037 wa 20 year
456038 wa 200
45603

488805 work yayyy
488806 work ye
488807 work ye im
488808 work yea
488809 work yeah
488810 work year
488811 work yearbook
488812 work yesterday
488813 work yey
488814 work yo
488815 work youd
488816 work youll
488817 work youtub
488818 work youv
488819 work yuck
488820 work yucki
488821 work yuk
488822 work3
488823 worka
488824 workagain
488825 workahol
488826 workal
488827 workand
488828 workanoth
488829 workaround
488830 workat
488831 workbench
488832 workblah
488833 workboo
488834 workbook
488835 workboooo
488836 workbor
488837 workbut
488838 workcant
488839 workcant wait
488840 workd
488841 workday
488842 workdont
488843 worker
488844 worker comp
488845 worker just
488846 worker strike
488847 workfeel
488848 workflow
488849 workfor
488850 workforc
488851 workgo
488852 workgonna
488853 workgotta
488854 workhad
488855 workhav
488856 workhop
488857 worki
488858 worki dont
488859 worki dont wan
488860 worki feel
488861 worki hate
488862 worki miss
488863 worki need
488864 worki want
48

In [76]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import classification_report


nb_model = MultinomialNB()
nb_model.fit(X_train_tdif, y_train)
y_pred = nb_model.predict(X_test_tdif)
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           0       0.78      0.77      0.78    159815
           1       0.77      0.78      0.78    160185

    accuracy                           0.78    320000
   macro avg       0.78      0.78      0.78    320000
weighted avg       0.78      0.78      0.78    320000



In [83]:
new_tweets = ["I LOVE THIS PRODUCT","This is bad"]

In [84]:
new_tweets_tdif= tfidf_Vector.transform(new_tweets)
nb_sentiments = nb_model.predict(new_tweets_tdif)

In [85]:
print(nb_sentiments)

[1 0]
